In [30]:
import proposal as pp
import numpy as np
from tqdm import tqdm

In [31]:
E_i = 1e5 # 1e9 # 1 PeV 
E_f = 1e1 # 1e5 # 100 GeV
n_events = 1000000 # 2500
    
deflection = [
    'bremsginneken', 
    'ioniznaive',
    'photoginneken',
    'epairginneken'] ### same as default
    
e_cut = 500 # 1e10
v_cut = 1e-3 # 1e-5
cont_rand = False
scattering_method = "moliere" # "highland"
deflection_type = "m_scat+stochastic"
  
table_path = "/Users/pascalgutjahr/.cache/PROPOSAL"    
# table_path = "/net/nfshome/home/pgutjahr/.cache/PROPOSAL" # vollmond
    
rnd_seed = 71530

interpol_nodes = 200

initial_direction = [0, 0, 1]

beta_brems = 1.0
beta_ioniz = 1.0
beta_epair = 1.0
beta_multiplescatter = 1.0
beta_photonuclear = 1.0

max_dist = 1e9

In [32]:
pp.InterpolationSettings.tables_path = table_path   # version 7
    
pp.InterpolationSettings.nodes_dndx_e = interpol_nodes
pp.InterpolationSettings.nodes_dndx_v = interpol_nodes

pp.RandomGenerator.get().set_seed(rnd_seed)
args = {
        "particle_def": pp.particle.MuMinusDef(),
        "target": pp.medium.Ice(),
        "interpolate": True,
        "cuts": pp.EnergyCutSettings(e_cut, v_cut, cont_rand)
        }

cross = pp.crosssection.make_std_crosssection(**args)
multiple_scatter = pp.make_multiple_scattering(scattering_method, args["particle_def"], args["target"], cross, True)

stochastic_deflect = []
for d in deflection:
    stochastic_deflect.append(pp.make_stochastic_deflection(d, 
    args["particle_def"], args["target"]))


collection = pp.PropagationUtilityCollection()
collection.displacement = pp.make_displacement(cross, True)
collection.interaction = pp.make_interaction(cross, True)
collection.time = pp.make_time(cross, args["particle_def"], True)
collection.decay = pp.make_decay(cross, args["particle_def"], True)



collection.scattering = pp.scattering.ScatteringMultiplier(
    multiple_scatter, 
    stochastic_deflect, 
    beta_multiplescatter, 
    [(pp.particle.Interaction_Type.brems, beta_brems), (pp.particle.Interaction_Type.ioniz, beta_ioniz), 
    (pp.particle.Interaction_Type.epair, beta_epair), (pp.particle.Interaction_Type.photonuclear, beta_photonuclear)])


utility = pp.PropagationUtility(collection = collection)
detector = pp.geometry.Sphere(pp.Cartesian3D(0,0,0), 1e20) # version 7
density_distr = pp.density_distribution.density_homogeneous(args["target"].mass_density)


prop = pp.Propagator(args["particle_def"], [(detector, utility, density_distr)])

init_state = pp.particle.ParticleState()
init_state.position = pp.Cartesian3D(0, 0, 0) # version 7
init_state.direction = pp.Cartesian3D(initial_direction[0], initial_direction[1], initial_direction[2]) # version 7

In [ ]:
for i in tqdm(range(n_events)):
    init_state.energy = E_i # initial energy in MeV
    track = prop.propagate(init_state, max_distance = max_dist, min_energy = E_f) # max_dist=1e9

  0%|                                                                                                                                                             | 50/1000000 [00:00<1:49:54, 151.63it/s]

[2022-04-25 17:16:50.939] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.11209545780319 MeV.
[2022-04-25 17:16:50.975] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.92938537562944 MeV.
[2022-04-25 17:16:51.067] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.8768428194119 MeV.
[2022-04-25 17:16:51.084] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.42780413986821 MeV.
[2022-04-25 17:16:51.194] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.6455196948947 MeV.


  0%|                                                                                                                                                            | 103/1000000 [00:00<1:38:58, 168.38it/s]

[2022-04-25 17:16:51.232] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.83068266740628 MeV.
[2022-04-25 17:16:51.290] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.77532860084312 MeV.
[2022-04-25 17:16:51.296] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.6606088262476 MeV.
[2022-04-25 17:16:51.377] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.76515588946367 MeV.
[2022-04-25 17:16:51.420] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.18245938446249 MeV.
[2022-04-25 17:16:51.425] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.03902771347781 MeV.


  0%|                                                                                                                                                            | 139/1000000 [00:00<1:37:10, 171.48it/s]

...

 34%|████████████████████████████████████████████████████▏                                                                                                      | 336480/1000000 [30:20<57:33, 192.12it/s]

[2022-04-25 17:47:10.773] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.8856148478381 MeV.
[2022-04-25 17:47:10.831] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.80256486480084 MeV.
[2022-04-25 17:47:10.836] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.7133934634561 MeV.
[2022-04-25 17:47:10.885] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.61522464549718 MeV.
[2022-04-25 17:47:10.920] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.75949388250721 MeV.
[2022-04-25 17:47:10.931] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.121239601863 MeV.
[2022-04-25 17:47:10.958] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 111.74008777357987 MeV.


 34%|████████████████████████████████████████████████████▏                                                                                                      | 336540/1000000 [30:20<58:08, 190.19it/s]

[2022-04-25 17:47:11.170] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.73254758014208 MeV.
[2022-04-25 17:47:11.323] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.55275371973245 MeV.
[2022-04-25 17:47:11.380] [proposal.interaction] [warning] No stochastic interaction possible for initial energy 112.05813425708757 MeV.


 34%|████████████████████████████████████████████████████▏                                                                                                      | 336560/1000000 [30:20<58:08, 190.19it/s]

In [ ]:
track.track_types()